## ELEX 4653 Final Exam

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

#### Question 1

Define a function `ls2len(l)`
that is passed a list of strings.  The function should return a list containing 
_twice_ the length of
each item in `l`.

For example `ls2len(["a", "abc", ""])` would return `[2, 6, 0]`.


#### Question 2

Define a function `dic2list(d)`
that is passed a dictionary `d` containing keys and values that are strings.
The function should return a list containing each key concatenated with the corresponding value.

For example, `dic2list({'key':'value', 'A':"1", '*':'*', 'DEF':'345'})` would return `['keyvalue', 'A1', '**', 'DEF345']`.

#### Question 3

Declare a class named 
`grower`
whose constructor (`__init__(self)`) takes no other arguments and contains one member function named `next()` that returns
the next in a sequence of 
alternating strings of 'A' and 'B', starting with 'A'.

For example:
```
o = grower()
print(o.next(), o.next(), o.next(), o.next())
```
would print `A B A B`.

#### Question 4


Write a function `capitalized(l)` that takes a list of strings `l` and returns another list 
containing only the strings whose first letter is upper-case and whose last letter is lower-case.

For example, `capitalized(['A', 'Ba', 'zebrA', 'animal', 'Days'])` would return
`['Ba', 'Days']`.


#### Question 5


Define a string named `myrea` containing a regular expression that matches a string _starting_ with: 

* the letters TP,
* optionally, the letter C
* three or four digits
* followed by one of the letters L, M or N.

For example, it would match: `TP000M`, `TPC1234L`, or `TP1234NX`
but not `' TPC1234L'`, `TPX1234L`, `TP1234`, or `TP12L`.


In [6]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    import traceback
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.search(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.search(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    
    import math
    def roundn(num, n):
        return 0 if not num else round(num, -int(math.floor(math.log10(abs(num)))) + (n - 1))

    def ch(s,n=(1,1)):
        return randwords(1,chars=s,nl=n)[0]

    def Q1():
        f,a = ls2len,randwords(randint(5,8))
        oa = copy.deepcopy(a)
        r = f(a)
        return r,f"{f.__name__}({repr(oa)}) returns {repr(r)}"   
        
    def Q2():
        f,a = dic2list,{randwords(1)[0]:randwords(1)[0] for i in range(randint(3,5))}
        oa = copy.deepcopy(a)
        r = f(a)
        return sorted(r),f"{f.__name__}({repr(oa)}) returns {repr(r)}"
    
    def Q3():
        o = grower()
        r = [o.next() for i in range(randint(5,9))]
        return r,f"next() returns {repr(r)}"
    
    def Q4():
        f,a = capitalized,[ch(string.ascii_uppercase,(0,1))+randwords(1)[0]+ch(string.ascii_uppercase,(0,1)) for i in range(randint(5,8))]
        oa = copy.deepcopy(a)
        r = f(a)
        return r,f"{f.__name__}({repr(oa)}) returns {repr(r)}"
        
    def Q5():    
        d = ( [f"TP{ch('C',(0,1))}{ch('0123456789',(3,4))}{ch('LMN',(1,2))}" for i in range(5)] , 
              ( ' TPC1234L', 'TPX1234L', 'TP12L', 'TPC1234C', ) )    
        checkre(myrea,*d)
        return 0,0

    hashvalues = '''
FKfOgghRwSohsTDpXT4EpK5k5wiBQhMHpKM588lT
KaV79tftu5zejbBp1H7wwl9nQzkLmFuGSLosqk0l
kxVA8/IJtB5PkxVAtB5PkxVAwoh2tB5PkxVAwoh2
/BVodhloUOo6q1ESoBlUKi6yIKT/5JIqmba2y7In
qwW6qwW6qwW6qwW6qwW6qwW6qwW6qwW6qwW6qwW6
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                traceback.print_exc()
                err = f"Error during test {n}: {e}"               
        if testing:
            newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)